# Get TNRIS LiDAR Collections, Collection Tiles and Tile URLs

 - Created by:   __Andy Carter, PE__
 >andy.carter@austin.utexas.edu

 - Created On:   __8 Aug 2022__<br><br>
 - Last revised:  __Verison 1.0  // Released 8 Aug 2022__<br><br>
 
 - Purpose:
 >From the TNRIS Web API (https://api.tnris.org/api/v1) fetch the geojson of the boundaries of all the collections that have LiDAR data.  These are the 'Elevation, Lidar' and the 'Lidar' data sets.  From the TNRIS mapserver (https://mapserver.tnris.org), get an index of tiles.  From the TNRIS Web API build URLs of tiles to download.
 
 
Inspiration for this workflow came from pseudocode provided by Daniel Hardesty Lewis.  Check it out at https://github.com/dhardestylewis/terrain_aggregator/issues/41#issuecomment-1207481378 --- Thanks Daniel --- you rock!


***
### 1.0 References

In [1]:
import requests
import geopandas as gpd
import pandas as pd
from shapely.geometry import shape
import re

***
### 2.0 Output Paths

In [2]:
# boundary of all of the lidar and 'elevation, lidar' collections
str_output_geojson_path = r'C:\test\tnris_lidar_collections.geojson'

# boundary of the tiles (quarter quads) in a single collection (from GUID)
str_tiles_geojson_path = r'C:\test\collection_tiles.geojson'

# 'best in time and space' collection output
str_best_in_time_path = r'C:\test\collection_best_in_time_and_space.geojson'

***
### 3.0 Get Collections

In [3]:
# create a geodataframe form the returned json.  Note that the returned json file has a list in the
# 'results' portion of the returned dictionary.

def fn_get_gdf_from_tnris_api(str_url):
    
    r = requests.get(str_url)
    dict_data = r.json()

    # convert the dictionary to a list in the 'results'
    list_data = dict_data.get("results")

    for d in list_data:
        d['the_geom'] = shape(d['the_geom'])

    gdf = gpd.GeoDataFrame(list_data).set_geometry('the_geom')
    gdf = gdf.set_crs(epsg=4326, inplace=True)
    
    return gdf

In [4]:
str_url = r'https://api.tnris.org/api/v1/collections_catalog.json?category='

# get a geodataframe of the 'Elevation, Lidar' collections
str_url_cat_elev_lidar = str_url + 'Elevation,Lidar'
gdf_category_1 = fn_get_gdf_from_tnris_api(str_url_cat_elev_lidar)

# get a geodataframe of the 'Lidar' collections
str_url_cat_lidar = str_url + 'Lidar'
gdf_category_2= fn_get_gdf_from_tnris_api(str_url_cat_lidar)

# combine the two geodataframes
gdf_lidar = pd.concat([gdf_category_1, gdf_category_2])

In [5]:
gdf_lidar.to_file(str_output_geojson_path, driver="GeoJSON")
gdf_lidar.explore()

***
### 4.0 Get Index of a Single Collection

In [6]:
# use TNRIS' mapserver to get the boundary of the tiles (quarter quads) for a single collection

#https://mapserver.tnris.org/?
#  map=/tnris_mapfiles/download_areas.map&
#  SERVICE=WFS&VERSION=2.0.0&
#  REQUEST=GetFeature&
#  TYPENAMES=collection_query&
#  outputformat=geojson&
#  SRSNAME=EPSG:4326&
#  Collection=6ddcc1e6-2059-4fa2-a2cf-4ab163e2c97e

In [7]:
# example: get the tile index for collection_id '6ddcc1e6-2059-4fa2-a2cf-4ab163e2c97e' --- 2019 Hurricane LiDAR
str_collection_id = '6ddcc1e6-2059-4fa2-a2cf-4ab163e2c97e'


# get the tiles for one collection

str_tiles_url = r'https://mapserver.tnris.org/?map=/tnris_mapfiles/download_areas.map&'
str_tiles_url += 'SERVICE=WFS&VERSION=2.0.0&'
str_tiles_url += 'REQUEST=GetFeature&'
str_tiles_url += 'TYPENAMES=collection_query&'
str_tiles_url += 'outputformat=geojson&'
str_tiles_url += 'SRSNAME=EPSG:4326&'
str_tiles_url += 'Collection='

# collection_id for the 2019 Hurricane LiDAR
str_tiles_url += str_collection_id

r = requests.get(str_tiles_url)
dict_data = r.json()

# convert the dictionary to a list in the 'results'
list_data = dict_data.get("features")

for d in list_data:
    d['geometry'] = shape(d['geometry'])

gdf_tiles = gpd.GeoDataFrame(list_data).set_geometry('geometry')
gdf_tiles = gdf_tiles.set_crs(epsg=4326, inplace=True)

In [8]:
# returns 'properties' as a dictionary

# get list of dictionaries
list_dict = gdf_tiles.properties.values.tolist()

# create dataframe of dictionaries
df_properties = pd.DataFrame(list_dict)

# merge the dataframe into the geodataframe by index
gdf_tiles = gdf_tiles.join(df_properties)

gdf_tiles = gdf_tiles.drop(['properties'], axis=1)

In [9]:
#gdf.to_file(str_tiles_geojson_path, driver="GeoJSON")
gdf_tiles.explore()

***
### 5.0 Get a single quarter qaud lidar tile url (zip of multiple LAZ tiles)

In [10]:
# get the area_type_id for the first tile in the collection
str_area_type_id = gdf_tiles.iloc[0]['area_type_id']

# need the collection name to create urls of tiles to download

# build a url to the tnris api to get name - like 'usgs19-70cm-hurricane' for 
# collection '6ddcc1e6-2059-4fa2-a2cf-4ab163e2c97e'

str_tnris_api_url = r'https://api.tnris.org/api/v1/resources?collection_id='
str_tnris_api_url += str_collection_id
str_tnris_api_url += '&area_type_id=' + str_area_type_id

r = requests.get(str_tnris_api_url)
dict_data = r.json()

# convert the dictionary to a list in the 'results'
list_data = dict_data.get("results")

# get the first resource url
str_resource_url = list_data[0]['resource']

# parse the last item in the url
str_filename = str_resource_url.rsplit('/', 1)[-1]

# everything up to the first '_' is the collection name
str_collection_name = re.search("^[^_]*", str_filename).group(0)

In [11]:
# get tile area code from the first polygon - could be another polygon
str_tile_area_code = gdf_tiles.iloc[0]['area_code']

In [12]:
# https://data.tnris.org/6ddcc1e6-2059-4fa2-a2cf-4ab163e2c97e/resources/usgs19-70cm-hurricane_2997364_lpc.zip

# build the download url for lpc.zip of tile
str_single_tile_url = r'https://data.tnris.org/'
str_single_tile_url += str_collection_id + r'/resources/'
str_single_tile_url += str_collection_name + "_"
str_single_tile_url += str_tile_area_code + "_lpc.zip"

In [13]:
str_single_tile_url

'https://data.tnris.org/6ddcc1e6-2059-4fa2-a2cf-4ab163e2c97e/resources/usgs19-70cm-hurricane_2996164_lpc.zip'

***
### 6.0 Build "best-in-time-and-space" from the collections returned

In [14]:
# read in the geojson to geopandas
gdf_collections = gpd.read_file(str_output_geojson_path)

# union of all the items in the input polygons
gdf_collections['new_column'] = 0
gdf_union = gdf_collections.dissolve(by='new_column')

# remove all cols from the gdf_union dataframe expect geometry
gdf_union = gdf_union[['geometry']]

# remove the '-' from the 'acquisition_date' col
gdf_collections['acquisition_date'] = gdf_collections['acquisition_date'].str.replace(r'\D', '')

# convert the date field to an integer
gdf_collections['acquisition_date'] = gdf_collections['acquisition_date'].astype(int)

C:\Users\civil\AppData\Local\Temp\ipykernel_9520\842083948.py:12: FutureWarning: The default value of regex will change from True to False in a future version.
  gdf_collections['acquisition_date'] = gdf_collections['acquisition_date'].str.replace(r'\D', '')


In [15]:
int_count_collections = len(gdf_collections)
int_max_count = int_count_collections

while int_count_collections > 0:
    # get index of the maximun value in 'acquisition_date'
    max_index = gdf_collections['acquisition_date'].idxmax()
    
    # get a geodataframe of the most collection currently remaining
    gdf_most_current = gdf_collections

    # remove all the rows except the most current
    for index,row in gdf_most_current.iterrows():
        if index != max_index:
            # remove this row from the dataframe
            gdf_most_current = gdf_most_current.drop(index)
            
    # intersect the gdf_most_current with the with the remaining union
    gdf_most_current_intersect = gdf_most_current.overlay(gdf_union, how='intersection')
    
    if int_count_collections == int_max_count:
        gdf_best_in_time = gdf_most_current_intersect
    else:
        # if the intersected polygon was an area/is polygon/ is multi-polygon
        gdf_best_in_time = pd.concat([gdf_best_in_time,gdf_most_current_intersect])
    
    # remove the gdf_most_current from the gdf_union
    # polygon of the remaining 'merged area'
    gdf_merge_difference = gdf_union.overlay(gdf_most_current, how='difference')
    
    gdf_union = gdf_merge_difference
    # remove all cols from the gdf_union dataframe expect geometry
    gdf_union = gdf_union[['geometry']]
    
    # remove the row from gdf_collections
    gdf_collections = gdf_collections.drop(max_index)
    
    int_count_collections -= 1
    
# TODO - 20220809 - UserWarning: `keep_geom_type=True` in overlay resulted in 1 dropped 
# geometries of different geometry types than df1 has. Set `keep_geom_type=False` to retain all geometries
# Likely do to intersecting topology errors of GeoCollection (multiple types of items, polygons, linestrings, etc..)

C:\Users\civil\anaconda3\envs\pdal\lib\site-packages\geopandas\geodataframe.py:2196: UserWarning: `keep_geom_type=True` in overlay resulted in 1 dropped geometries of different geometry types than df1 has. Set `keep_geom_type=False` to retain all geometries
  return geopandas.overlay(
C:\Users\civil\anaconda3\envs\pdal\lib\site-packages\geopandas\geodataframe.py:2196: UserWarning: `keep_geom_type=True` in overlay resulted in 1 dropped geometries of different geometry types than df1 has. Set `keep_geom_type=False` to retain all geometries
  return geopandas.overlay(
C:\Users\civil\anaconda3\envs\pdal\lib\site-packages\geopandas\geodataframe.py:2196: UserWarning: `keep_geom_type=True` in overlay resulted in 1 dropped geometries of different geometry types than df1 has. Set `keep_geom_type=False` to retain all geometries
  return geopandas.overlay(
C:\Users\civil\anaconda3\envs\pdal\lib\site-packages\geopandas\geodataframe.py:2196: UserWarning: `keep_geom_type=True` in overlay resulted in

In [16]:
gdf_best_in_time.to_file(str_best_in_time_path, driver="GeoJSON")
gdf_best_in_time.explore(tooltip=['name','acquisition_date'])